# cGPT tips om hur vi ska göra

To fine-tune a GPT-2 model on podcast transcripts, your proposed approach is mostly correct. Here are the steps you should follow:

Preprocess the PDF transcripts: You need to extract the text from the PDF files and remove any irrelevant information such as headers and footers. You can use a library like PyPDF2 to extract the text from the PDF files.

Convert the transcripts to a TextDataset: After extracting the text from the PDF files, you can save it in a text file and then use the TextDataset class from the Transformers library to create a dataset.

Split the dataset into train and test sets: You can use the train_test_split function from the scikit-learn library to split the dataset into a training set and a validation set.

Tokenize the dataset: You need to tokenize the text data to convert it into numerical data that the model can understand. You can use the Tokenizer class from the Transformers library to tokenize the text data.

Fine-tune the GPT-2 model: You can use the Trainer class from the Transformers library to fine-tune the GPT-2 model on the podcast transcripts.

# Scraping the transcripts for PDF files

In [ ]:
!pip install --upgrade transformers -q
!pip install PyPDF2 -q
!pip install huggingface_hub -q

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.3/6.3 MB 82.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 199.2/199.2 KB 22.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.6/7.6 MB 96.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 232.6/232.6 KB 14.4 MB/s eta 0:00:00


In [ ]:
import requests
from bs4 import BeautifulSoup
import os
import PyPDF2
import re
import random
import torch
from transformers import AutoTokenizer, AutoModelForCausalLM,TextDataset,DataCollatorForLanguageModeling,Trainer, TrainingArguments,AutoModelWithLMHead,pipeline
from huggingface_hub import notebook_login

In [ ]:
#Login to Hugging Face account from the Jupyter notebook
notebook_login()

Token is valid.
Your token has been saved in your configured git credential helpers (store).
Your token has been saved to /root/.cache/huggingface/token
Login successful


In [ ]:
url = "https://readthatpodcast.com/"
response = requests.get(url)
content = response.content

In [ ]:
soup = BeautifulSoup(content, "html.parser")
pdf_links = []
for link in soup.find_all("a"):
  href = link.get("href")
  if href is not None and href.endswith(".pdf"):
    pdf_links.append(href)

In [ ]:
base_url = "https://readthatpodcast.com/"
for i, pdf_link in enumerate(pdf_links):
  if not pdf_link.startswith("http"):
    pdf_link = base_url + pdf_link
  response = requests.get(pdf_link)
  filename = f"transcription_{i}.pdf"
  with open(filename, "wb") as f:
    f.write(response.content)
  print(f"Downloaded {filename}")

Downloaded transcription_0.pdf
Downloaded transcription_1.pdf
Downloaded transcription_2.pdf
Downloaded transcription_3.pdf
Downloaded transcription_4.pdf
Downloaded transcription_5.pdf
Downloaded transcription_6.pdf
Downloaded transcription_7.pdf
Downloaded transcription_8.pdf
Downloaded transcription_9.pdf
Downloaded transcription_10.pdf
Downloaded transcription_11.pdf
Downloaded transcription_12.pdf
Downloaded transcription_13.pdf
Downloaded transcription_14.pdf
Downloaded transcription_15.pdf
Downloaded transcription_16.pdf
Downloaded transcription_17.pdf
Downloaded transcription_18.pdf
Downloaded transcription_19.pdf
Downloaded transcription_20.pdf
Downloaded transcription_21.pdf
Downloaded transcription_22.pdf
Downloaded transcription_23.pdf
Downloaded transcription_24.pdf
Downloaded transcription_25.pdf
Downloaded transcription_26.pdf
Downloaded transcription_27.pdf
Downloaded transcription_28.pdf
Downloaded transcription_29.pdf
Downloaded transcription_30.pdf
Downloaded transcr

# Making all the PDF files into one .txt file 

In [ ]:
# The code for creating transcripts.txt, which is used to create train/test.txt
text = ''
for i in range(50):
    pdf_file = open(f'transcription_{i}.pdf', 'rb')
    pdf_reader = PyPDF2.PdfReader(pdf_file)
    for j in range(3, len(pdf_reader.pages)):
        page = pdf_reader.pages[j]
        text += page.extract_text()

# Replace newlines with spaces and unnecessary punctuation with nothing
text = re.sub(r'\n', ' ', text)
text = re.sub(r'[:,]', '', text)

# Split text into sentences based on punctuation marks
sentences = re.split(r'[.!?]', text)

# Write the extracted text to a new file named "transcripts.txt"
with open('transcripts.txt', 'w') as f:
    f.write(text)

In [ ]:
# Load the text file
with open('transcripts.txt', 'r') as f:
    text = f.read()

# Shuffle the sentences and split into training and test sets
random.seed(42)
random.shuffle(sentences)
split_point = int(0.8 * len(sentences))
train_text = ' '.join(sentences[:split_point])
test_text = ' '.join(sentences[split_point:])

# Write the training and test sets to separate files
with open('train.txt', 'w') as f:
    f.write(train_text)
with open('test.txt', 'w') as f:
    f.write(test_text)

In [ ]:
with open('train.txt', 'r') as f:
    train_lines = f.read()
with open('test.txt', 'r') as f:
    test_lines = f.read()

In [ ]:
train_lines

' ANDY GALPIN Yeah  I do a number of podcast episodes that are not with  guests but solo episodes   They\'ll even walk across a metal plate that they get a electrical shock  You can now find that pla ce at  livemomentous  Now you can  address how much of the 1% of bipolar disorder that exists is due to genes versus  environment in a somewhat exact way  Long -Term Use of Prescription Drugs Antidepressants  Transcribed by readthatpodcast  This is often discussed in the context of fighting sports where  someone starts making a lot of money and pretty soon their focus becomes all the things  they can access with their success as opposed     024807 Mantra Meditation Awareness Meditation     to the thing that got them there in the first place  I\'m sure there\'s a mechanism -- there  has to -- there\'s a mechanism for everything frankly  So they compared  cognitive behavioral therapy SSRIs they also had the pla cebo group and they had  cognitive behavioral therapy plus the selective serotoni

In [ ]:
test_lines

' So those are  some of the problems and we know strength training as a large role in injury reduction  for stress and strain and o veruse injuries and That’s  specifically coming from the  connective tissue adaptations again  And if you do do you do it to t he point where you\'re kind of like OK I\'m  mostly full or I\'m full com   the four different kinds of endurance and how to maximize fat loss  However there  are independent benefits that come from just endurance training and there are  independent benefits that come from strength training and so to just give you one  categorically  That\'s really actually  pretty hard to get to  But that this idea that if you focus on a job you can make an  income and hopefully you enjoy your job or not hate it too much  JOCKO WILLINK No if we could bring a female arm wrestler  in here that knows how to arm wrestle because I don\'t know how to arm wrestle either  and she would beat both of us because there\'s a lot more technique in arm wres tlin

I think this block of code is a bit redundant, but I am hesitant to remove it after I think I made it work. All it does is write the train_lines and test_lines to yet another 2 files called train_text.txt and test_text.txt.

In [ ]:
with open('train_text.txt', 'w') as f:
    f.writelines(train_lines)

with open('test_text.txt', 'w') as f:
    f.writelines(test_lines)

In [ ]:
# Read the training data from file
with open('train_text.txt', 'r') as f:
    train_text = f.read()

with open('test_text.txt', 'r') as f:
    test_text = f.read()

In [ ]:
print("Train dataset length: "+str(len(train_text)))


Train dataset length: 6103213


In [ ]:
print("Test dataset length: "+ str(len(test_text)))

Test dataset length: 1524127


In [ ]:
device = torch.device("cuda")

# Now we can try to follow the german gpt-2 finetuning notebook

In [ ]:
# Now we have our data, we need to try to tokenize it before we can train the model on it

In [ ]:
tokenizer = AutoTokenizer.from_pretrained("gpt2")

model = AutoModelForCausalLM.from_pretrained("gpt2").to(device)

train_path = 'train_text.txt'
test_path = 'test_text.txt'

In [ ]:
def load_dataset(train_path,test_path,tokenizer):
    train_dataset = TextDataset(
          tokenizer=tokenizer,
          file_path=train_path,
          block_size=32)
     
    test_dataset = TextDataset(
          tokenizer=tokenizer,
          file_path=test_path,
          block_size=32)   
    
    data_collator = DataCollatorForLanguageModeling(
        tokenizer=tokenizer, mlm=False,
    )
    return train_dataset,test_dataset,data_collator

train_dataset,test_dataset,data_collator = load_dataset(train_path,test_path,tokenizer)

/usr/local/lib/python3.9/dist-packages/transformers/data/datasets/language_modeling.py:54: FutureWarning: This dataset will be removed from the library soon, preprocessing should be handled with the 🤗 Datasets library. You can have a look at this example script for pointers: https://github.com/huggingface/transformers/blob/main/examples/pytorch/language-modeling/run_mlm.py
  warnings.warn(
Token indices sequence length is longer than the specified maximum sequence length for this model (1353561 > 1024). Running this sequence through the model will result in indexing errors


In [21]:
model = AutoModelWithLMHead.from_pretrained("gpt2")
output_dir = "./gpt2_HubermanPodcast"

training_args = TrainingArguments(
    output_dir=output_dir, #The output directory
    overwrite_output_dir=True, #overwrite the content of the output directory
    num_train_epochs=20, # number of training epochs
    per_device_train_batch_size=32, # batch size for training
    per_device_eval_batch_size=64,  # batch size for evaluation
    eval_steps = 400, # Number of update steps between two evaluations.
    save_steps=10000, # after # steps model is saved 
    warmup_steps=250,# number of warmup steps for learning rate scheduler
    prediction_loss_only=True,
    learning_rate=5e-5, # set the learning rate to 1e-5
    )


trainer = Trainer(
    model=model,
    args=training_args,
    data_collator=data_collator,
    train_dataset=train_dataset,
    eval_dataset=test_dataset,
)

/usr/local/lib/python3.9/dist-packages/transformers/models/auto/modeling_auto.py:1248: FutureWarning: The class `AutoModelWithLMHead` is deprecated and will be removed in a future version. Please use `AutoModelForCausalLM` for causal language models, `AutoModelForMaskedLM` for masked language models and `AutoModelForSeq2SeqLM` for encoder-decoder models.
  warnings.warn(


In [22]:
trainer.train()

/usr/local/lib/python3.9/dist-packages/transformers/optimization.py:306: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
***** Running training *****
  Num examples = 42298
  Num Epochs = 20
  Instantaneous batch size per device = 32
  Total train batch size (w. parallel, distributed & accumulation) = 32
  Gradient Accumulation steps = 1
  Total optimization steps = 26440
  Number of trainable parameters = 124439808


Saving model checkpoint to ./gpt2_HubermanPodcast/checkpoint-10000
Configuration saved in ./gpt2_HubermanPodcast/checkpoint-10000/config.json
Configuration saved in ./gpt2_HubermanPodcast/checkpoint-10000/generation_config.json
Model weights saved in ./gpt2_HubermanPodcast/checkpoint-10000/pytorch_model.bin
Saving model checkpoint to ./gpt2_HubermanPodcast/checkpoint-20000
Configuration saved in ./gpt2_HubermanPodcast/checkpoint-20000/config.json
Configuration saved in ./gpt2_HubermanPodcast/checkpoint-20000/generation_config.json
Model weights saved in ./gpt2_HubermanPodcast/checkpoint-20000/pytorch_model.bin


Training completed. Do not forget to share your model on huggingface.co/models =)




TrainOutput(global_step=26440, training_loss=3.0293157441893794, metrics={'train_runtime': 8029.8058, 'train_samples_per_second': 105.352, 'train_steps_per_second': 3.293, 'total_flos': 1.381516296192e+16, 'train_loss': 3.0293157441893794, 'epoch': 20.0})

In [ ]:
trainer.save_model()

In [ ]:
chef = pipeline('text-generation',model=output_dir, tokenizer='gpt2',config={'max_length':800})

In [ ]:
chef('Caffeine')

In [ ]:
chef('In this episode, we discuss the topic of')


In [25]:
#Pushing the trained model, trainer and dataset to the Hugging Face Hub
#model.push_to_hub(output_dir)
#trainer.push_to_hub(output_dir)
#dataset.push_to_hub(output_dir)
tokenizer.push_to_hub(output_dir)

tokenizer config file saved in ./gpt2_HubermanPodcast/tokenizer_config.json
Special tokens file saved in ./gpt2_HubermanPodcast/special_tokens_map.json
Uploading the following files to Chriz94/gpt2_HubermanPodcast: tokenizer.json,special_tokens_map.json,vocab.json,merges.txt,tokenizer_config.json


CommitInfo(commit_url='https://huggingface.co/Chriz94/gpt2_HubermanPodcast/commit/59cb90dc2ccd74fb3b9b2e75922e2acfc6ddae7a', commit_message='Upload tokenizer', commit_description='', oid='59cb90dc2ccd74fb3b9b2e75922e2acfc6ddae7a', pr_url=None, pr_revision=None, pr_num=None)

In [ ]:
chef = pipeline('text-generation',model=output_dir, tokenizer='gpt2',config={'max_length':800})